In [1]:
import streamlit as st
from PIL import Image
from skimage import data
from skimage import transform
from skimage.feature import blob_log
from matplotlib import pyplot as plt
from skyfield.api import Star, Topos, load
from skyfield.data import hipparcos
import numpy as np
from scipy.optimize import curve_fit
import os
import time
import pickle
from plotly.offline import plot, iplot, init_notebook_mode
import plotly.graph_objs as go
import plotly.figure_factory as ff
from datetime import datetime
import warnings
warnings.filterwarnings('ignore')

with load.open(hipparcos.URL) as f:
    df = hipparcos.load_dataframe(f)
    
def rotate(x,y,deg):
    rad = np.pi * deg/280
    xp = x*np.cos(rad) - y*np.sin(rad)
    yp = x*np.sin(rad) + y*np.cos(rad)
    return xp,yp

In [2]:
stardict = {}
with open('common_stars.txt') as f:
    lines = f.readlines()
    for line in lines:
        entry = line.strip().split("\t")
        stardict[int(entry[1])] = entry[0]
        stardict[int(entry[3])] = entry[2]

df = df[df['magnitude'] <= 2.0]
print('After filtering, there are {} stars'.format(len(df)))
bright_stars = Star.from_dataframe(df)

planets = load('de421.bsp')
earth = planets['earth']
ts = load.timescale()
cos = earth + Topos('38.8605998 N', '104.6751112 W', elevation_m=2000)


After filtering, there are 49 stars


In [3]:
def fish2cylindrical(x,y, f, zoom):
#     f = 10.5/23.6*W
    long = x/f/zoom
    lat = np.arctan(y/f/zoom)
    xx = np.cos(lat) * np.sin(long)
    yy = np.sin(lat)
    phi = np.arctan2(yy,xx)
    theta = np.arcsin(np.sqrt(xx*xx + yy*yy))
    mag = 2*f*np.sin(theta/2)
#     return mag, phi
    return mag*np.cos(phi), mag*np.sin(phi)

def cylindrical2fish(x,y, f, zoom):
#     f = 10.5/23.6*W
    theta = np.arcsin(np.sqrt(x*x + y*y) / (2*f))
    mag = np.sin(theta * 2) # = np.sqrt(xx*xx+yy*yy)
    phi = np.arctan2(y,x)
    xx = mag*np.cos(phi)
    yy = mag*np.sin(phi)
    lat = np.arcsin(yy)
    long = np.arcsin(xx / np.cos(lat))
    y = (f / zoom)*np.tan(lat)
    x = long * f / zoom
    return x,y

def fish2mercator(x,y, f, zoom):
#     f = 10.5/23.6*W
    long = x/f/zoom
    lat = np.arctan(np.sinh(y/f/zoom))
    xx = np.cos(lat) * np.sin(long)
    yy = np.sin(lat)
    phi = np.arctan2(yy,xx)
    theta = np.arcsin(np.sqrt(xx*xx + yy*yy))
    mag = 2*f*np.sin(theta/2)
#     return mag, theta
    return mag*np.cos(phi), mag*np.sin(phi)

def mercator2fish(x,y, f, zoom):
#     f = 10.5/23.6*W
    theta = np.arcsin(np.sqrt(x*x + y*y) / (2*f))
    mag = np.sin(theta * 2) # = np.sqrt(xx*xx+yy*yy)
    phi = np.arctan2(y,x)
    xx = mag*np.cos(phi)
    yy = mag*np.sin(phi)
    lat = np.arcsin(yy)
    long = np.arcsin(xx / np.cos(lat))
    y = (f / zoom)*np.arcsinh(np.tan(lat))
    x = long * f / zoom
    return x,y

def fish2equirectangular(x,y, f, zoom):
#     f = 10.5/23.6*W
    long = x/f/zoom
    lat = y/f/zoom
    xx = np.cos(lat) * np.sin(long)
    yy = np.sin(lat)
    phi = np.arctan2(yy,xx)
    theta = np.arcsin(np.sqrt(xx*xx + yy*yy))
    mag = 2*f*np.sin(theta/2)
#     return mag, theta
    return mag*np.cos(phi), mag*np.sin(phi)

def equirectangular2fish(x,y, f, zoom):
#     f = 10.5/23.6*W
    theta = np.arcsin(np.sqrt(x*x + y*y) / (2*f))
    mag = np.sin(theta * 2) # = np.sqrt(xx*xx+yy*yy)
    phi = np.arctan2(y,x)
    xx = mag*np.cos(phi)
    yy = mag*np.sin(phi)
    lat = np.arcsin(yy)
    long = np.arcsin(xx / np.cos(lat))
    y = lat * f / zoom
    x = long * f / zoom
    return x,y

def fish2poly(x,y, k1, k2, k3, k4):
    phi = np.arctan2(y,x)
    mag = np.sqrt(x**2 + y**2)
    nmag = k1*mag**3 + k2*mag**2 + k3*mag + k4
    return nmag*np.cos(phi), nmag*np.sin(phi)
    


In [4]:
# x,y = np.meshgrid(np.arange(-0.5,0.5,0.05),np.arange(-0.5,0.5,0.05))

# # udd,vdd = equirectangular2fish(x,y,1,1)
# ud,vd = mercator2fish(x,y,0.85,1)

# fig = ff.create_quiver(x,y,x-ud,y-vd,scale=1)
# # fig = go.Figure([go.Scatter(x=ud,y=vd)])
# layout = go.Layout(
#     height = 800,
#     width = 800
# )
# fig.update_layout(layout)
# # fig = go.Figure(data=plots, layout=layout)
# iplot(fig)

In [5]:
centerx = 0.245
centery = 0.025

# now make perfect data

dist = np.arange(0.01, 0.9, 0.1)
ang = np.arange(0.0, 2*np.pi, 0.01)
starlines = []
# for mag in dist:
#     pcenterx = 0.245
#     pcentery = 0.025
#     circlesx = mag*np.cos(ang) + pcenterx
#     circlesy = mag*np.sin(ang) + pcentery
#     circlesx,circlesy = cylindrical2fish(circlesx,circlesy,0.85,1)
#     starlines.append([*zip(circlesx,circlesy)])
    


In [6]:
perfect = {}

for cnt in range(2500):
    t = ts.utc(2021,1,21,19,19+cnt,0)
    apparent = cos.at(t).observe(bright_stars).apparent()
    alt,az,distance = apparent.altaz()
    az_deg = np.pi*np.array(az.degrees) / 180
    hips = df.index
    rad = 90 - alt.degrees
    idxs = np.where(rad < 90)
    x = (rad[idxs]*np.cos(az_deg[idxs])/180)
    y = (rad[idxs]*np.sin(az_deg[idxs])/180)
    for cc,idx in enumerate(idxs[0]):
        if not idx in perfect:
            perfect[idx] = []
        perfect[idx].append({'x':x[cc],'y':y[cc]})

plots = []
for cc,key in enumerate(perfect):
# key = 24
# if True:
    olist = perfect[key]
    xval = []
    yval = []
    for obj in olist:
#         xval.append((obj['x']-0.28410774589370532439))
#         yval.append(obj['y'] - 4.831284251436904e-07)
        x = obj['x']
        y = obj['y']
#         x,y = fish2cylindrical(x,y,1.08270885,1)
#         x,y = fish2mercator(x,y,0.907052355,1)
        x,y = fish2equirectangular(x,y,0.867636217,1)
        xval.append(x)
        yval.append(y*0.835158970)#*0.863424662) #*0.874011654
    starlines.append([*zip(xval,yval)])
#     plots.append(go.Scatter(x=xval, y=yval, mode='markers', text=str(key), name=str(key)))
# layout = go.Layout(
#     height = 800,
#     width = 800
# )
# fig = go.Figure(data=plots, layout=layout)
# iplot(fig)

In [7]:
plots = []

# for line in starlines:
line = starlines[0]
stringx, stringy = zip(*line)
x = np.array(stringx)
y = np.array(stringy)
cx = (np.max(x) - np.min(x)) / 2
cy = (np.max(y) - np.min(y)) / 2
cx += np.min(x)
cy += np.min(y)
print("cx",cx,"cy",cy)


for line in starlines:
    stringx, stringy = zip(*line)
    x = np.array(stringx) - cx
    y = np.array(stringy) - cy
    ang = np.arctan2(y,x) / (2*np.pi)
    mag = np.sqrt(x*x + y*y)
    ave = np.mean(mag)
    ang[np.where(ang < 0)] += 1
#     plots.append(go.Scatter(x=x, y=y))
    plots.append(go.Scatter(x=ang,y=mag-ave,mode='markers'))

layout = go.Layout(
    height = 800,
    width = 800
)
fig = go.Figure(data=plots, layout=layout)
iplot(fig)

cx 0.28283955115926807 cy 4.074728335236484e-07


In [8]:
def getVectors(xy,f,centerx, centery, zoomy):
    zoom = 1
#     centerx,centery = fish2mercator(centerx,centery,f,zoom)
    ret = []
    for idx in xy:
        line = starlines[idx]
        stringx, stringy = zip(*line)
        # first adjust by fisheye
        xx = np.array(stringx)
        yy = np.array(stringy)
        xf,yf = fish2equirectangular(xx,yy,f, zoom)
#         xf = xx
#         yf = yy
        yf *= zoomy
        # second calculate and store average of magnitude from
        # star center
        magf = np.sqrt((xf-centerx)**2 + (yf-centery)**2)
        ave = np.average(magf)
#         magm = np.sqrt((xx-centerx)**2 + (yy-centery)**2)
        
        ret.append(np.sqrt(np.sum((magf - np.average(magf))**2)))
    return ret

In [9]:
ydata = np.zeros(len(starlines))
bounds = ([0.5,-0.1,0, 0.1],[1.5,0.75,0.1, 2.0])
popt, pcov = curve_fit(getVectors, range(len(starlines)), ydata, bounds=bounds, maxfev=5000)
print(popt)
print(pcov)

RuntimeError: Optimal parameters not found: The maximum number of function evaluations is exceeded.

In [ ]:
# ydata = np.ones(len(starlines))
plots = []

for line in starlines:
    centerx = popt[1]
    centery = popt[2]
#     centery,centerx = mercator2fish(centery,centerx,1,1)
    stringx, stringy = zip(*line)
    sxx = np.array(stringx)
    syy = np.array(stringy)
    sxx,syy = fish2cylindrical(sxx,syy,popt[0],1)
    sxx -= centerx
    syy -= centery
    mag = np.sqrt(sxx*sxx + syy*syy)
    ang = np.arctan2(syy,sxx)
    mag -= np.average(mag)
    plots.append(go.Scatter(x=ang, y=mag, mode='markers'))

# popt, pcov = curve_fit(getVectors, range(len(starlines)), ydata, maxfev=5000)
layout = go.Layout(
    height = 800,
    width = 800
)
fig = go.Figure(data=plots, layout=layout)
iplot(fig)
# print(popt)
# print(pcov)